# **Sentiment Analysis with Deep Learning using BERT**


## **What is BERT?**

BERT is a large-scale transformer-based Language Model that can be finetuned for a variety of tasks.

For more information, the original paper can be found here (https://arxiv.org/abs/1810.04805).

HuggingFace documentation (https://huggingface.co/transformers/model_doc/bert.html)

In [161]:
import pandas as pd
import numpy as np
import csv
from nltk.cluster import KMeansClusterer, euclidean_distance
from nltk.corpus import wordnet as wn
from nltk.stem import WordNetLemmatizer
from itertools import product, filterfalse
from nltk import stem

In [162]:
DATA_PATH = "./"
wasabi_songs = pd.read_csv(
    DATA_PATH + "wasabi_songs.csv",
    sep="\t",
    usecols=[
        "_id",
        "abstract",
        "albumTitle",
        "album_genre",
        "artist",
        "genre",
        "has_emotion_tags",
        "lastfm_id",
        "title",
    ],
)

In [163]:
wasabi_songs.head()

_id abstract             albumTitle  \
0  ObjectId(5714dec325ac0d8aee3804e7)      NaN  How Ace Are Buildings   
1  ObjectId(5714dec325ac0d8aee3804e8)      NaN  How Ace Are Buildings   
2  ObjectId(5714dec325ac0d8aee3804e9)      NaN  How Ace Are Buildings   
3  ObjectId(5714dec325ac0d8aee3804ea)      NaN  How Ace Are Buildings   
4  ObjectId(5714dec325ac0d8aee3804eb)      NaN  How Ace Are Buildings   

        album_genre artist genre  has_emotion_tags lastfm_id          title  
0  Alternative Rock      A   NaN             False       NaN     Turn It Up  
1  Alternative Rock      A   NaN             False       NaN        Foghorn  
2  Alternative Rock      A   NaN             False       NaN  Cheeky Monkey  
3  Alternative Rock      A   NaN             False       NaN          No. 1  
4  Alternative Rock      A   NaN             False       NaN       Bad Idea

In [164]:
wasabi_songs['has_emotion_tags'].value_counts()

False    2012157
True       87397
Name: has_emotion_tags, dtype: int64

In [367]:
emotion_tags = pd.read_pickle(DATA_PATH + "lastfm_id_to_emotion_tags.pickle")
#print(emotion_tags)
my_dict = {}
i = 0
for k,v in emotion_tags.items():
    # if i==2:
    #     break
    # print(k,v)
    max_val = v[0][1]
    max_mood = v[0][0]
    for j in range(len(v)):
        #print(v[j][1])
        if v[j][1]> max_val:
            max_val = v[j][1]
            max_mood = v[j][0]
    #print(max_mood)
    my_dict[k] = max_mood
    #i+=1
#print(my_dict)
#emotion_tags = {k: dict(v) for k, v in emotion_tags.items()}
#print((emotion_tags))

{'TRRRRCH128F9342C72': [('happy', 3), ('happiness', 2), ('mellow', 1)], 'TRRRRNA128F42948D2': [('party', 0)], 'TRRRRLE128F147C97D': [('fun', 100)], 'TRRRRYK128F93229FA': [('soothing', 4), ('relaxing', 4), ('fun', 4)], 'TRRRRGT128F4288741': [('smooth', 66), ('mellow', 0)], 'TRRRUFD12903CD7092': [('poignant', 50)], 'TRRRUXN128F932DAE8': [('fury', 4), ('aggressive', 4), ('rage', 4)], 'TRRRUTV12903CEA11B': [('party', 2), ('sad', 1), ('energetic', 1), ('happy', 0)], 'TRRRUCQ12903CEA6CB': [('melancholic', 12), ('melancholy', 12), ('heartbreak', 12), ('soft', 12), ('bittersweet', 12)], 'TRRRULH128F92CDB2E': [('aggressive', 12)], 'TRRRIVO128F930867B': [('mellow', 35), ('melancholy', 5), ('relaxing', 5)], 'TRRRIVC12903CA6C5A': [('mellow', 33), ('quiet', 11)], 'TRRRIUK12903CFB054': [('melancholic', 33)], 'TRRRILO128F422FFED': [('party', 12)], 'TRRRNBX128F42524EF': [('fun', 12), ('party', 0)], 'TRRRNUC128EF35E22F': [('mellow', 50)], 'TRRRNGS12903CD16D9': [('mellow', 25)], 'TRRRNHH128F422B1FF': [(

In [313]:
emotion_frame = pd.DataFrame(list(my_dict.items()), columns = ['lastfm_id', 'emotion'])
#emotion_frame.fillna(0, inplace=True)
#emotion_frame.columns = ['emotions']
print(len(emotion_frame))
print(emotion_frame.head())

83279
            lastfm_id   emotion
0  TRRRRCH128F9342C72     happy
1  TRRRRNA128F42948D2     party
2  TRRRRLE128F147C97D       fun
3  TRRRRYK128F93229FA  soothing
4  TRRRRGT128F4288741    smooth


In [366]:
d = [True, True]
x = sum(d)
print(x)

2


In [314]:
print(emotion_frame['emotion'].value_counts())

mellow         11795
party           5851
sexy            5837
fun             4764
happy           4482
               ...  
vigorous           1
funereal           1
pesimism           1
ebullient          1
incredulous        1
Name: emotion, Length: 190, dtype: int64


In [315]:
# happy_lst = ['happy', 'happiness', 'party', 'ebullient', 'fun', 'excitement', 'amiable', 'excite', 'desire', 'celebrate', 'festive', 'romantic', 'jovial', 'zest', 'cheerup', 'cheering', 'celebratory', 'merry', 'rambunctious', 'boisterous', 'confident', 'gleeful', 'happy songs', 'funny', 'happy music', 'playful', 'autumnal', 'cheerful', 'warm', 'passionate', 'passion', 'humor', 'humorous', 'savage', 'enthusiastic', 'joyous', 'exciting', 'joyful', 'cheer', 'cheer-up', 'lively', 'rollicking', 'jolly', 'high spirits', 'glad', 'bright']
# sad_lst = ['poignant','sad', 'unhappy', 'melancholic', 'dejected', 'funereal', 'despondent', 'incredulous', 'dreary', 'sceptic', 'pesimism', 'miserable', 'sorry', 'mourn', 'nervous', 'weep', 'brokenheart', 'pesimistic', 'severe', 'introverted', 'lamenting', 'sob', 'contemplate', 'sobbing', 'weeping', 'volatile', 'plaintive', 'anxiety', 'frightening', 'lament', 'melancholy', 'unfortunate', 'weltschmerz', 'tough', 'heartbreak', 'tragic', 'bittersweet', 'grim', 'dark', 'contemplative', 'dreamy', 'funeral', 'misery', 'tragedy', 'mournful', 'fiery', 'elegiac',  'touching', 'campy', 'introvert', 'introspective', 'bleak', 'heartbroken', 'sadness', 'angst-ridden', 'depressing', 'delicate', 'sorrow', 'moving', 'depressive', 'angst', 'blue', 'gloomy', 'cry', 'depressed', 'grief', 'somber', 'crying', 'bitter', 'heartbreaking', 'detached', 'harsh']
# calm_lst = ['mellow', 'soothing', 'relaxing', 'quietly', 'quietness','springlike', 'sooth', 'calmness', 'untroubled', 'unworried', 'smooth', 'quiet', 'soft', 'relax', 'peaceful', 'calmed', 'calm', 'gentle', 'relaxed', 'comfort', 'soothe', 'serenity', 'peace', 'serene', 'visceral', 'tender', 'tranquil']
# sexy_lst = ['fury', 'aggressive', 'ardor', 'rage', 'enraged', 'outrageous', 'feverish', 'revolt', 'feral', 'unconcerned', 'animated', 'wintry', 'hostile', 'vigor', 'rough', 'troubled', 'thrilling', 'intensive', 'crusty', 'outraged', 'fighting', 'annoyed', 'vigorous', 'anguished', 'confrontational', 'exhilarating', 'rowdy', 'energetic', 'furious', 'military', 'sexy', 'fear', 'desperate', 'angry', 'intense', 'fight', 'apocalyptic', 'anger', 'eerie', 'fierce', 'macabre', 'rebel', 'anxious', 'spooky', 'tense', 'martial', 'mad', 'annoying', 'excited', 'aggression', 'silly', 'march', 'peppy', 'conflict', 'thrill', 'rebellious', 'paranoid', 'arousing', 'marching' ]

In [316]:
happy_lst = ['happy', 'happiness', 'happy songs', 'happy music','party']
sad_lst = ['sadness', 'unhappy', 'melancholic', 'melancholy', 'unhappy']
calm_lst = ['calm', 'comfort', 'quiet', 'serene', 'mellow', 'chill out', 'soothing']
sexy_lst = ['sexy', 'arousing', 'ardor', 'fun']

In [317]:
i = 0
for index, row in emotion_frame.iterrows():
    #print(row['emotions'])
    if row['emotion'] in happy_lst:
        row['emotion'] = 'happy'
    elif row['emotion'] in sad_lst:
        row['emotion'] = 'sad'
    elif row['emotion'] in calm_lst:
        row['emotion'] = 'calm'
    elif row['emotion'] in sexy_lst:
        row['emotion'] = 'sexy'




In [318]:
df = ((emotion_frame['emotion']).value_counts())
print(df.head(200))
emotion_frame.head()

calm           13901
sad            10943
happy          10744
sexy           10608
dark            3468
               ...  
vigorous           1
funereal           1
untroubled         1
ebullient          1
incredulous        1
Name: emotion, Length: 174, dtype: int64


lastfm_id emotion
0  TRRRRCH128F9342C72   happy
1  TRRRRNA128F42948D2   happy
2  TRRRRLE128F147C97D    sexy
3  TRRRRYK128F93229FA    calm
4  TRRRRGT128F4288741  smooth

In [329]:
index_names_c = emotion_frame[(emotion_frame['emotion'] != 'calm')].index
index_names_s = emotion_frame[(emotion_frame['emotion'] != 'happy')].index
index_names_h = emotion_frame[(emotion_frame['emotion'] != 'sad')].index
index_names_ss = emotion_frame[(emotion_frame['emotion'] != 'sexy')].index
print(type(index_names_ss))
#final = index_names_c + index_names_s + index_names_h + index_names_ss
#print(final)
e1 = emotion_frame.copy()
e2 = emotion_frame.copy()
e3 = emotion_frame.copy()
e4 = emotion_frame.copy()
e1.drop(index_names_c, inplace=True)
e2.drop(index_names_s, inplace=True)
e3.drop(index_names_h, inplace=True)
e4.drop(index_names_ss, inplace=True)
e1.head()
len(e4)
frames = [e1, e2, e3, e4]
result = pd.concat(frames)
#final = pd.merge(e1,e2,e3,e4)
#emotion_frame.drop(final, inplace = True)
#print(final.head())
result.head()
print(len(result))

<class 'pandas.core.indexes.numeric.Int64Index'>
46196


In [346]:
new_df =  pd.merge(wasabi_songs, result, on='lastfm_id')
new_df.head()
print(len(new_df))
new_df.head()

51265


_id abstract                  albumTitle  \
0  ObjectId(5714dec325ac0d8aee38058d)      NaN                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)      NaN                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)      NaN                      Panama   
3  ObjectId(5714dec325ac0d8aee38090f)      NaN  And Their Name Was Treason   
4  ObjectId(5714dec325ac0d8aee380915)      NaN    For Those Who Have Heart   

     album_genre             artist genre  has_emotion_tags  \
0            NaN        A Balladeer   NaN              True   
1            NaN        A Balladeer   NaN              True   
2            NaN        A Balladeer   NaN              True   
3  Post-Hardcore  A Day To Remember   NaN              True   
4  Post-Hardcore  A Day To Remember   NaN              True   

            lastfm_id                           title emotion  
0  TRSWIJK128F147228E                  Winterschläfer    calm  
1  TRWAAES128F147228F                        Robin II     sad  
2  TRXFSFN128F1472291                         Hamburg     sad  
3  TRPRUME12903CFE793             You Had Me At Hello    sexy  
4  TRBEEEP128F426C17D  The Plot To Bomb The Panhandle    sexy

In [347]:
my_lyrics = pd.read_csv('lyrics_dataset.csv')
my_lyrics.drop(['emotion'], axis = 1)
my_lyrics.head()

_id                  albumTitle  \
0  ObjectId(5714dec325ac0d8aee38058d)                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)                      Panama   
3  ObjectId(5714dec325ac0d8aee3805c8)               Broken Dreams   
4  ObjectId(5714dec325ac0d8aee38090d)  And Their Name Was Treason   

               artist           lastfm_id  \
0         A Balladeer  TRSWIJK128F147228E   
1         A Balladeer  TRWAAES128F147228F   
2         A Balladeer  TRXFSFN128F1472291   
3  A Band Called Pain  TRTGWUO128F42869E9   
4   A Day To Remember  TRTPZCV12903CFE78A   

                                               title emotion  \
0                                     Winterschläfer    calm   
1                                           Robin II     sad   
2                                            Hamburg     sad   
3                                               Holy  energy   
4  You Should Have Killed Me When You Had The Chance  energy   

                                              lyrics  
0  That was your mom who I just informed\nNow go ...  
1  Well, it's been a few days now, so how have yo...  
2  And then there was\nA flood of tears in secrec...  
3  Yeah yeah yeah\nThe midnight sky is black and ...  
4  EPISODE 8 - THE PRINCE OF WINTERFELLEXT: WINTE...

In [348]:
my_lyrics = my_lyrics.drop(['emotion'], axis = 1)
my_lyrics.head()

_id                  albumTitle  \
0  ObjectId(5714dec325ac0d8aee38058d)                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)                      Panama   
3  ObjectId(5714dec325ac0d8aee3805c8)               Broken Dreams   
4  ObjectId(5714dec325ac0d8aee38090d)  And Their Name Was Treason   

               artist           lastfm_id  \
0         A Balladeer  TRSWIJK128F147228E   
1         A Balladeer  TRWAAES128F147228F   
2         A Balladeer  TRXFSFN128F1472291   
3  A Band Called Pain  TRTGWUO128F42869E9   
4   A Day To Remember  TRTPZCV12903CFE78A   

                                               title  \
0                                     Winterschläfer   
1                                           Robin II   
2                                            Hamburg   
3                                               Holy   
4  You Should Have Killed Me When You Had The Chance   

                                              lyrics  
0  That was your mom who I just informed\nNow go ...  
1  Well, it's been a few days now, so how have yo...  
2  And then there was\nA flood of tears in secrec...  
3  Yeah yeah yeah\nThe midnight sky is black and ...  
4  EPISODE 8 - THE PRINCE OF WINTERFELLEXT: WINTE...

In [349]:
new_df.head()

_id abstract                  albumTitle  \
0  ObjectId(5714dec325ac0d8aee38058d)      NaN                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)      NaN                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)      NaN                      Panama   
3  ObjectId(5714dec325ac0d8aee38090f)      NaN  And Their Name Was Treason   
4  ObjectId(5714dec325ac0d8aee380915)      NaN    For Those Who Have Heart   

     album_genre             artist genre  has_emotion_tags  \
0            NaN        A Balladeer   NaN              True   
1            NaN        A Balladeer   NaN              True   
2            NaN        A Balladeer   NaN              True   
3  Post-Hardcore  A Day To Remember   NaN              True   
4  Post-Hardcore  A Day To Remember   NaN              True   

            lastfm_id                           title emotion  
0  TRSWIJK128F147228E                  Winterschläfer    calm  
1  TRWAAES128F147228F                        Robin II     sad  
2  TRXFSFN128F1472291                         Hamburg     sad  
3  TRPRUME12903CFE793             You Had Me At Hello    sexy  
4  TRBEEEP128F426C17D  The Plot To Bomb The Panhandle    sexy

In [350]:
new_df1 =  pd.merge(new_df, my_lyrics, on='lastfm_id')
new_df1.head()
print(len(new_df1))
new_df1.head()

49533


_id_x abstract                albumTitle_x  \
0  ObjectId(5714dec325ac0d8aee38058d)      NaN                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)      NaN                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)      NaN                      Panama   
3  ObjectId(5714dec325ac0d8aee38090f)      NaN  And Their Name Was Treason   
4  ObjectId(5714dec325ac0d8aee380915)      NaN    For Those Who Have Heart   

     album_genre           artist_x genre  has_emotion_tags  \
0            NaN        A Balladeer   NaN              True   
1            NaN        A Balladeer   NaN              True   
2            NaN        A Balladeer   NaN              True   
3  Post-Hardcore  A Day To Remember   NaN              True   
4  Post-Hardcore  A Day To Remember   NaN              True   

            lastfm_id                         title_x emotion  \
0  TRSWIJK128F147228E                  Winterschläfer    calm   
1  TRWAAES128F147228F                        Robin II     sad   
2  TRXFSFN128F1472291                         Hamburg     sad   
3  TRPRUME12903CFE793             You Had Me At Hello    sexy   
4  TRBEEEP128F426C17D  The Plot To Bomb The Panhandle    sexy   

                                _id_y                albumTitle_y  \
0  ObjectId(5714dec325ac0d8aee38058d)                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)                      Panama   
3  ObjectId(5714dec325ac0d8aee38090f)  And Their Name Was Treason   
4  ObjectId(5714dec325ac0d8aee380915)    For Those Who Have Heart   

            artist_y                         title_y  \
0        A Balladeer                  Winterschläfer   
1        A Balladeer                        Robin II   
2        A Balladeer                         Hamburg   
3  A Day To Remember             You Had Me At Hello   
4  A Day To Remember  The Plot To Bomb The Panhandle   

                                              lyrics  
0  That was your mom who I just informed\nNow go ...  
1  Well, it's been a few days now, so how have yo...  
2  And then there was\nA flood of tears in secrec...  
3  I'm missing you so much, I'll see you die toni...  
4  I've learned to let go\nCome on\n\nHere's a mi...

In [356]:
#final = new_df1['artist_x', 'title_x', 'lastfm_id', 'emotion', 'lyrics']
d = new_df1[['artist_x', 'title_x', 'lastfm_id', 'emotion', 'lyrics']]
d.head()
len(d)

49533

In [358]:
d.to_csv('final.csv')

In [182]:
summaries = pd.read_pickle(DATA_PATH + "id_to_summary_lines.pickle")
# print(summaries)
summary_dict = {}
i = 0
for k, v in summaries.items():
    concat_summary = ' '.join(v)
    obj_id = 'ObjectId('+k+')'
    summary_dict[obj_id] = concat_summary
    #print(obj_id,concat_summary)

#print(summary_dict)

In [183]:
sumary_pd = pd.DataFrame(list(summary_dict.items()), columns = ['_id', 'summary'])
sumary_pd.head()

_id  \
0  ObjectId(5714dec325ac0d8aee3806e4)   
1  ObjectId(5714dec325ac0d8aee3806ee)   
2  ObjectId(5714dec325ac0d8aee380ff2)   
3  ObjectId(5714dec325ac0d8aee380ff4)   
4  ObjectId(5714dec325ac0d8aee380ff5)   

                                             summary  
0  'cause you were always on the run from the dar...  
1  i'll let go if you just tell me i will forget ...  
2  lie to get just what i need lie and smile to g...  
3  and not to pull your halo down around your nec...  
4  such a lovely color for you while i just sit a...

In [184]:
final_pd =  pd.merge(new_df, sumary_pd, on='_id')
print(len(final_pd))
print(final_pd['emotion'].value_counts())
final_pd.head()

7909
happy     2670
calm      2120
sad       1617
energy    1502
Name: emotion, dtype: int64


_id abstract           albumTitle  \
0  ObjectId(5714dec325ac0d8aee380a70)      NaN         Demo Sampler   
1  ObjectId(5714dec325ac0d8aee380a73)      NaN  One Cell In The Sea   
2  ObjectId(5714dec325ac0d8aee380a75)      NaN  One Cell In The Sea   
3  ObjectId(5714dec325ac0d8aee380a76)      NaN  One Cell In The Sea   
4  ObjectId(5714dec325ac0d8aee380a79)      NaN  One Cell In The Sea   

  album_genre         artist genre  has_emotion_tags           lastfm_id  \
0         Pop  A Fine Frenzy   NaN              True  TRBPEZO128F4299263   
1         Pop  A Fine Frenzy   NaN              True  TRATATB128F427C7F2   
2         Pop  A Fine Frenzy   NaN              True  TRLVGJF128F4299261   
3         Pop  A Fine Frenzy   NaN              True  TREYOJA128F4299262   
4         Pop  A Fine Frenzy   NaN              True  TRQVHMD128F4299265   

               title emotion  \
0            Rangers    calm   
1  Come On, Come Out    calm   
2            Whisper    calm   
3      You Picked Me    calm   
4       Think Of You    calm   

                                             summary  
0  and the rangers stream we are the rabbits but ...  
1  watching the sky you're watching a painting co...  
2  yeah you stay real close i will reach you i'm ...  
3  is you blow me away hiding out behind the leav...  
4  and i think of you i think of you yeah but you...

In [185]:
print(len(new_df))
new_df.head()

87397


_id abstract                  albumTitle  \
0  ObjectId(5714dec325ac0d8aee38058d)      NaN                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)      NaN                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)      NaN                      Panama   
3  ObjectId(5714dec325ac0d8aee3805c8)      NaN               Broken Dreams   
4  ObjectId(5714dec325ac0d8aee38090d)      NaN  And Their Name Was Treason   

     album_genre              artist genre  has_emotion_tags  \
0            NaN         A Balladeer   NaN              True   
1            NaN         A Balladeer   NaN              True   
2            NaN         A Balladeer   NaN              True   
3    Heavy Metal  A Band Called Pain   NaN              True   
4  Post-Hardcore   A Day To Remember   NaN              True   

            lastfm_id                                              title  \
0  TRSWIJK128F147228E                                     Winterschläfer   
1  TRWAAES128F147228F                                           Robin II   
2  TRXFSFN128F1472291                                            Hamburg   
3  TRTGWUO128F42869E9                                               Holy   
4  TRTPZCV12903CFE78A  You Should Have Killed Me When You Had The Chance   

  emotion  
0    calm  
1     sad  
2     sad  
3  energy  
4  energy

In [186]:
import lyricsgenius as lg
file = open("auto_.txt", "w")
genius = lg.Genius('yVRmGfk7S4oHDTlo-MWYEy4_xq7hk6d1Hu1mJ7inJNhZH7qPKvTurgqz6JUlZtSE', skip_non_songs=True, excluded_terms=["(Remix)", "(Live)"], remove_section_headers=True)
song = genius.search_song("Rangers", 'A Fine Frenzy')

Searching for "Rangers" by A Fine Frenzy...
Done.


In [187]:
from requests.exceptions import Timeout

In [203]:
temp_df = new_df.copy()
temp_df['lyrics'] = np.NAN
i =-1
for index, row in temp_df.iterrows():
    i+=1
    retries = 0
    while retries < 3:
        try:
            song = genius.search_song(row['title'], row['artist'])
        except Timeout as e:
            retries += 1
            continue
        if song is not None:
            temp_df.loc[i,'lyrics'] = song.lyrics
            #temp_df[row['title'],['lyrics']] = temp_df['lyrics'].replace(np.NAN, song.lyrics)
            #temp_df['lyrics'].append(song.lyrics)
            temp_df.to_csv('my_lyrics.csv')
        else:
            #temp_df['lyrics'] = temp_df['lyrics'].replace(np.NAN, song.lyrics)
            temp_df.to_csv('my_lyrics.csv')
        break
        
            
            
    
    

Searching for "Winterschläfer" by A Balladeer...
Done.
Searching for "Robin II" by A Balladeer...
Done.
Searching for "Hamburg" by A Balladeer...
Done.
Searching for "Holy" by A Band Called Pain...
Done.
Searching for "You Should Have Killed Me When You Had The Chance" by A Day To Remember...
Done.
Searching for "You Had Me At Hello" by A Day To Remember...
Done.
Searching for "1958" by A Day To Remember...
Done.
Searching for "The Plot To Bomb The Panhandle" by A Day To Remember...
Done.
Searching for "I'm Made Of Wax, Larry, What Are You Made Of?" by A Day To Remember...
Done.
Searching for "Have Faith In Me" by A Day To Remember...
Done.
Searching for "If It Means A Lot To You" by A Day To Remember...
Done.
Searching for "The Life" by A Dream Too Late...
Done.
Searching for "Have I Never" by A Few Good Men...
Done.
Searching for "Rangers" by A Fine Frenzy...
Done.
Searching for "Rangers" by A Fine Frenzy...
Done.
Searching for "Come On, Come Out" by A Fine Frenzy...
Done.
Searching 

ConnectionError: ('Connection aborted.', ConnectionResetError(54, 'Connection reset by peer'))

In [208]:
print(i)
i = 10172

10180


In [209]:
for index, row in temp_df.iterrows():
    
    if index >=10172:
        i+=1
        retries = 0
        while retries < 3:
            try:
                song = genius.search_song(row['title'], row['artist'])
            except Timeout as e:
                retries += 1
                continue
            if song is not None:
                temp_df.loc[i,'lyrics'] = song.lyrics
                #temp_df[row['title'],['lyrics']] = temp_df['lyrics'].replace(np.NAN, song.lyrics)
                #temp_df['lyrics'].append(song.lyrics)
                temp_df.to_csv('my_lyrics.csv')
            else:
                #temp_df['lyrics'] = temp_df['lyrics'].replace(np.NAN, song.lyrics)
                temp_df.to_csv('my_lyrics.csv')
            break
        

Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "Hanging On The Telephone" by Blondie...
Done.
Searching for "One Way Or Another" by Blondie...
Done.
Searching for "One Way Or Another" by Blondie...
Done.
Searching for "One Way Or Another" by Blondie...
Done.
Searching for "One Way Or Another" by Blondie...
Done.
Searching for "One Way Or Another" by Blondie...
Done.
Searching for "Fade Away And Radiate" by Blondie...
Done.
Searching for "Fade Away And Radiate" by Blondie...
Done.
Searching for "Fade Away And Radiate" by Blondie...
Done.
Searching for "Fade Away And Radiate" by Blondie...
Done.
Searching for "Fade Away And Radiate" by Blondie...
Done.
Searchin

HTTPError: [Errno 503] 503 Server Error: Service Unavailable for url: https://genius.com/api/search/multi?q=Simple+Song+Of+Freedom+Bobby+Darin

In [215]:
my_pd = temp_df.copy()
print(len(my_pd))
my_pd.head()

87397


_id abstract                  albumTitle  \
0  ObjectId(5714dec325ac0d8aee38058d)      NaN                      Panama   
1  ObjectId(5714dec325ac0d8aee38058e)      NaN                      Panama   
2  ObjectId(5714dec325ac0d8aee380590)      NaN                      Panama   
3  ObjectId(5714dec325ac0d8aee3805c8)      NaN               Broken Dreams   
4  ObjectId(5714dec325ac0d8aee38090d)      NaN  And Their Name Was Treason   

     album_genre              artist genre  has_emotion_tags  \
0            NaN         A Balladeer   NaN              True   
1            NaN         A Balladeer   NaN              True   
2            NaN         A Balladeer   NaN              True   
3    Heavy Metal  A Band Called Pain   NaN              True   
4  Post-Hardcore   A Day To Remember   NaN              True   

            lastfm_id                                              title  \
0  TRSWIJK128F147228E                                     Winterschläfer   
1  TRWAAES128F147228F                                           Robin II   
2  TRXFSFN128F1472291                                            Hamburg   
3  TRTGWUO128F42869E9                                               Holy   
4  TRTPZCV12903CFE78A  You Should Have Killed Me When You Had The Chance   

  emotion                                             lyrics  
0    calm  That was your mom who I just informed\nNow go ...  
1     sad  Well, it's been a few days now, so how have yo...  
2     sad  And then there was\nA flood of tears in secrec...  
3  energy  Yeah yeah yeah\nThe midnight sky is black and ...  
4  energy  EPISODE 8 - THE PRINCE OF WINTERFELLEXT: WINTE...

In [216]:
my_pd = my_pd.drop_duplicates(subset=['artist', 'title'], keep='last')
print(len(my_pd))

59112


In [218]:
my_pd['emotion'].value_counts()

calm      16800
happy     16433
sad       15812
energy    10067
Name: emotion, dtype: int64

In [225]:
my_pd = my_pd.reset_index(drop = True)
my_pd.to_csv('temp.csv', index = False)

In [226]:
my_pd = pd.read_csv('temp.csv', index_col = False)
my_pd.head()

Unnamed: 0                                 _id abstract  \
0           0  ObjectId(5714dec325ac0d8aee38058d)      NaN   
1           1  ObjectId(5714dec325ac0d8aee38058e)      NaN   
2           2  ObjectId(5714dec325ac0d8aee380590)      NaN   
3           3  ObjectId(5714dec325ac0d8aee3805c8)      NaN   
4           4  ObjectId(5714dec325ac0d8aee38090d)      NaN   

                   albumTitle    album_genre              artist genre  \
0                      Panama            NaN         A Balladeer   NaN   
1                      Panama            NaN         A Balladeer   NaN   
2                      Panama            NaN         A Balladeer   NaN   
3               Broken Dreams    Heavy Metal  A Band Called Pain   NaN   
4  And Their Name Was Treason  Post-Hardcore   A Day To Remember   NaN   

   has_emotion_tags           lastfm_id  \
0              True  TRSWIJK128F147228E   
1              True  TRWAAES128F147228F   
2              True  TRXFSFN128F1472291   
3              True  TRTGWUO128F42869E9   
4              True  TRTPZCV12903CFE78A   

                                               title emotion  \
0                                     Winterschläfer    calm   
1                                           Robin II     sad   
2                                            Hamburg     sad   
3                                               Holy  energy   
4  You Should Have Killed Me When You Had The Chance  energy   

                                              lyrics  
0  That was your mom who I just informed\nNow go ...  
1  Well, it's been a few days now, so how have yo...  
2  And then there was\nA flood of tears in secrec...  
3  Yeah yeah yeah\nThe midnight sky is black and ...  
4  EPISODE 8 - THE PRINCE OF WINTERFELLEXT: WINTE...

In [234]:

for index, row in my_pd.iterrows():
    
    if index >=11000 and index<=20000:
        i+=1
        retries = 0
        while retries < 3:
            try:
                song = genius.search_song(row['title'], row['artist'])
            except Timeout as e:
                retries += 1
                continue
            if song is not None:
                my_pd.loc[index,'lyrics'] = song.lyrics
                #temp_df[row['title'],['lyrics']] = temp_df['lyrics'].replace(np.NAN, song.lyrics)
                #temp_df['lyrics'].append(song.lyrics)
                my_pd.to_csv('my_lyrics_latest.csv')
            else:
                #temp_df['lyrics'] = temp_df['lyrics'].replace(np.NAN, song.lyrics)
                my_pd.to_csv('my_lyrics_latest.csv')
            break
        

Searching for "Sielunvihollinen" by CMX...
Done.
Searching for "Palvelemaan Konetta" by CMX...
Done.
Searching for "Olet Tässä" by CMX...
Done.
Searching for "Kiusaajien Kiusaaja" by CMX...
Done.
Searching for "Resurssikysymys" by CMX...
Done.
Searching for "Kivinen Kirja" by CMX...
Done.
Searching for "What Happens On The Road Always Comes Home" by Coalesce...
Done.
Searching for "We Interrupt This Programme" by Coburn...
Done.
Searching for "Being From Jersey Means Never Having To Say You're Sorry" by Cobra Starship...
Done.
Searching for "The Church Of Hot Addiction" by Cobra Starship...
Done.
Searching for "It's Warmer In The Basement" by Cobra Starship...
Done.
Searching for "Keep It Simple" by Cobra Starship...
Done.
Searching for "Bring It (Snakes On A Plane)" by Cobra Starship...
Done.
Searching for "The Ballad Of Big Poppa And Diamond Girl" by Cobra Starship...
Done.
Searching for "You Can't Be Missed If You Never Go Away" by Cobra Starship...
Done.
Searching for "Damn You Loo

In [233]:
print(index)

59111
